In [1]:
from common import *
from given import *
import re

In [2]:
pd.set_option('display.max_colwidth', 115)

In [3]:
_N_ = pd.read_pickle(big_data/'trans/N10.pkl') #get_N()
_N_['headlineTagId'] = _N_.headlineTag.map(headlineTagIdAssign)

In [36]:
N = _N_small = _N_[('2015-01-01'<=_N_.time)&(_N_.time<'2015-04-01')]

In [10]:
from akamap import akamap
xAssetNames = set(assetNameIdAssign.series)
_flag = False
for x in akamap:
    if x not in xAssetNames:
        _flag = True
        print(x)
assert not _flag

# Helpers

In [12]:
ljust = lambda s: s.str.ljust(s.str.len().max())
def ljust_c(columns):
    if isinstance(columns, str):
        columns = [columns]
    def ljust_df(df):
        df = df.copy()
        for c in columns:
            df[c] = ljust(df[c])
        return df
    return ljust_df

In [13]:
def sample(k):
    def sample_k(df):
        n = len(df)
        samps = sorted(random.sample(range(n), k))
        return df.iloc[samps]
    return sample_k

# Notes and TODOs

In [14]:
'STCKa.O vs STCKb.O';

In [15]:
'''
stock matching algorithm:
    match whole
    loop take away one token from right and try match
    repeat above with symbols removed (add no space)
''';

In [16]:
'''
preprocessing pipeline:
    replace \ => [delete]
    replace ` => '
    convert numbers
    convert stock ticker symbols
    replace ... => #ellipsis
    replace . => [delete]
    replace -- => #dash
    replace [symbol not backslash] => [same symbol with spaces on either side]
    lowercase
    split
    remove stock endings words
    match stock name
        match canonical name in decreasing num words right to left
            also try get rid of symbol words inside decreasing word loop # also commas before Inc, Ltd
        repeat prev 2 lines with all aka names
            order of which choose aka names as follows:
                if aka maps to list, do canon name first, then the list in order
                if aka maps to one str, see if wordified the aka str is sublist of canon name,
                    if so, do canon name first, then aka name
                    else, do aka name first, then canon
    remove CORPORATION/INCORPORATED and the likes from after the stock mention #TODO
''';

# Preprocessing

In [17]:
def make_replacer(key_values):
    try:
        replace_dict = dict(key_values)
    except (TypeError, ValueError):
        replace_dict = {a: '' for a in key_values}
    replacement_function = lambda match: replace_dict[match.group(0)]
    pattern = re.compile("|".join([re.escape(k) for k, v in replace_dict.items()]), re.M)
    return lambda string: pattern.sub(replacement_function, string)

## real code

#### define some constants

In [20]:
corpFull = {
    'Incorporated': 'Inc',
    ',Incorporated': ',Inc',
    'Corporation': 'Corp',
    'Company': 'Co',
    'Limited': 'Ltd',
    ',Limited': ',Ltd',
    ',Limited Liability Company': 'LLC',
    ',Limited Liability Company': ',LLC',
    'Public Limited Company': 'PLC',
    ',Public Limited Company': ',PLC',
    'Limited Partnership': ['LP', 'L P'],
    ',Limited Partnership': [',LP', ', L P'],
    'Companies': 'Cos',
    'Societe anonyme': ['SA','S A'],
    'Naamloze vennootschap': ['NV', 'N V'],
    # AS A/S ASA full names don't show up in news
    'Aktiengesellschaft': 'AG',
}
corpAbbrMapFull = {}
for full, abbrs in corpFull.items():
    if isinstance(abbrs, str):
        abbrs = [abbrs]
    for abbr in abbrs:
        corpAbbrMapFull[abbr] = full
corpFull = list(corpFull.keys())
corpAbbr = 'Inc ,Inc Corp Co Ltd ,Ltd LLC ,LLC PLC ,PLC LP ,LP Cos SA ,SA NV ,NV ASA A/S AS PAO AG'.split()
corpAbbr += ['S A',', S A','L P','P L C','N V','SA de CV',',SA de CV']
corpSpec = 'co company cos companies'.split()

#### simple subs

In [21]:
if TEST:
    re_money = re.compile(r'(?<!\w)\$[0-9]+(,[0-9][0-9][0-9])*.?[0-9]*')
    re_money.search('hi :$5,666.00').group(0)
    re_year = re.compile(r'(?<![0-9])('+'|'.join(str(i) for i in range(1999, 2022))+')(?![0-9])')
    re_year.search('hi what 2009e  ').group()
    re_percent = re.compile(r'(?<!\w)[0-9]+(,[0-9][0-9][0-9])*\.?[0-9]*\%')
    re_percent.search('hi 66%').group()

In [22]:
class resub(metaclass=staticclass):
    @classmethod
    def replace(cls, text):
        return cls.re.sub(cls.put, text)

# stupid fucking re.sub interprets backslash+<char> as escape sequences IN THE REPLACEMENT STRING!
# like, bitch, I give you a string when I could have equally well given you a function, I want you to take it as it fck'ng is
    
class HPL(metaclass=staticclass): # headline @pipeline #TODO test the regexes
    class Money(resub):
        re = re.compile(r'[\$\¤\¥\£\€]\ ?[0-9]+(\,[0-9][0-9][0-9])*\.?[0-9]*')
        put = r'\\money'+'\\'*4
    class Percent(resub): # a percent number - if connected to words don't include
        re = re.compile(r'(?<!\w)[0-9]+(\,[0-9][0-9][0-9])*\.?[0-9]*\%')
        put = r'\\decimal'+'\\'*4
    class Year(resub): # any digits that look like dates will be replaced
        re = re.compile(r'(?<![0-9])('+'|'.join(str(i) for i in range(2008, 2020))+'|'
                        +'|'.join(fr"\'{i:02}" for i in range(8,20))+')(?![0-9])')
        put = r'\\year'+'\\'*4
    class Decimal(resub): # a number with decimals - if connected to words don't include
        re = re.compile(r'(?<!\w)[0-9]+(,[0-9][0-9][0-9])*\.[0-9]+(?!\w)')
        put = r'\\decimal'+'\\'*4
    class Count(resub): # a natural number - if connected to words don't include
        re = re.compile(r'(?<!\w)[0-9]+(,[0-9][0-9][0-9])*(?!\w)')
        def put(match):
            guy = match.group().replace(',', '')
            sz = str(len(guy) if guy[0] not in '01' else len(guy)-1)
            return '\\count\\' + sz + r'\\'
        
    class Misc(resub): # add spaces around symbols that are not backslash
        re = re.compile(r'[^\w\.\s\\]')
        put = lambda match: ' ' + match.group() + ' '
    
    # post wordify
    
    class Quarter(resub):
        re = re.compile(r'\ '+
            r'(q1|q2|q3|q4|(first|1st|second|2nd|third|3rd|fourth|4th)\ \ quarter|quarter\ \ \\count\\(0|1)\.)'+
        r'\ ')
        put = r' \\quarter\\labelled. '
    class Month(resub):
        re = re.compile(r'\ (january|jan|february|feb|march|mar|april|apr|may|june|jun|july|jul|august|aug|'+
                        r'september|sep|sept|october|oct|november|nov|december|dec)\ ')
        put = r' \\month. '
    
# put into HPL context: HPL.self (an assetNameId) and HPL.assets (container of assetNameIds)
    
@inside(HPL)
class Ticker(resub):
    re_lowercase = re.compile(r'[a-z]')
    def norm(ticker):
        ticker = Ticker.re_lowercase.sub('', ticker)
        return ticker[:ticker.index('.')] if '.' in ticker else ticker
    
    re = re.compile(r'<[A-Z]+[a-z]*.?[A-Z]*>')
    
    def put(match):
        try:
            codes = assetNameMapCodes[HPL.self]
        except KeyError:
            return r' \ticker\\ '
        normed = Ticker.norm(match.group()[1:-1]) # match.group() is of form <AAPL.O>
        if any(Ticker.norm(x)==normed for x in assetCodeIdAssign.series[list(codes)]):
            return r' \ticker\self\\ '
        else:
            return r' \ticker\\ '

In [23]:
@inside(HPL)
def listify(text):
    text = text.replace('\\','').replace('`',"'")
    text = compose(*[getattr(getattr(HPL,a),'replace') for a in ['Year','Money','Percent','Decimal','Count']])(text)
    text = HPL.Ticker.replace(text)
    text = text.replace('...',r' \ellipsis\\ ').replace('.','').replace('\\\\','.').replace('--','—')
    text = HPL.Misc.replace(text).lower()
    return text.split()

@inside(HPL)
def wordify(text):
    return ' '+'  '.join(HPL.listify(text))+' '

@inside(HPL)
def postproc(text):
    return compose(*[getattr(getattr(HPL,a),'replace') for a in ['Quarter','Month']])(text)

In [24]:
# store the wordified things inside one place

@inside(HPL, name='words')
class words(O()):
    cAbbr = list(map(HPL.wordify, corpAbbr))
    cFull = list(map(HPL.wordify, corpFull))
    cSpec = list(map(HPL.wordify, corpSpec))

_replace_corpwords = make_replacer(HPL.words.cAbbr)
_rp = lambda x: _replace_corpwords(HPL.wordify(x))
HPL.words.assetNameSeries = assetNameIdAssign.series.map(_rp)
HPL.words.akamap = {x: (list([_rp(y)]) if isinstance(y, str) else list(map(_rp, y))) for x,y in dict.items(akamap)}


# store the regex of wordified things in one place

@memoized
def _make_stock_ending():
    maybe = '('+'|'.join(re.escape(' '+a+' ') for a in HPL.words.cSpec)+')?'
    corps = '('+'|'.join(re.escape(a) for a in HPL.words.cAbbr+HPL.words.cFull)+')?'
    return maybe+corps

def make_regex_for_stock(words): #TODO save time by considering only relevant stock endings
    lst = words.split()
    def rec_make_sub_chain(lst):
        return re.escape(' '+lst[0]+' ') if len(lst)==1 else re.escape(' '+lst[0]+' ')+'('+rec_make_sub_chain(lst[1:])+')?'
    return re.compile(rec_make_sub_chain(lst)+_make_stock_ending())


@inside(HPL, name='regex')
class regex(O()):
    assetNameSeries = HPL.words.assetNameSeries.map(make_regex_for_stock)
    akamap = {x: list(map(make_regex_for_stock, y)) for x,y in dict.items(HPL.words.akamap)}

In [25]:
# @inside(HPL) 
# def match_stocks(words):
#     for asset in HPL.assets:
#         put = r'\asset\self.' if asset==HPL.self else r'\asset.'
#         assetWords = HPL.words.assetNameSeries.loc[asset]
#         for i in range(len(assetWords), 0, -1):
#             useWords = assetWords[:i]
#             k = 0
#             while k+i <= len(words):
#                 if words[k:k+i] == useWords:
#                     words[k:k+i] = [put]
#                 k += 1
#     return words

@inside(HPL)
def match_stocks(words):
    for asset in [HPL.self] + [a for a in HPL.assets if a!=HPL.self]:
        put = r' \\asset\\self. ' if asset==HPL.self else r' \\asset. '
        
        assetCanon = assetNameIdAssign.series.loc[asset]
        assetWords, assetRegex = HPL.words.assetNameSeries.loc[asset], HPL.regex.assetNameSeries.loc[asset]
        akaWords, akaRegex = HPL.words.akamap.get(assetCanon, []), HPL.regex.akamap.get(assetCanon, [])
        if len(akaWords)==0:
            assetRegexList = [assetRegex]
        elif len(akaWords)==1 and next(iter(akaWords)) not in assetWords:
            assetRegexList = [next(iter(akaRegex)), assetRegex]
        else:
            assetRegexList = [assetRegex] + list(akaRegex)
        
        for assetRegex in assetRegexList:
            words = assetRegex.sub(put, words)
    return words

In [26]:
def transform_headlines(*, N):
    ret = [None] * len(N)
    # idk probably save time looking up N's hash table:
    sourceIds, assetNameIds, inHeadline = N.sourceId.values, N.assetNameId.values, (N.firstMentionSentence==1).values
    hTags, hTagIds = N.headlineTag.values, N.headlineTagId.values
    new_i = 0 # this tracks grouping of sourceIds
    # basically, I see that same sourceIds are always consecutive. so every time I see new news item I walk down table
    # to see where the same news item ends, and collect all the assetNameIds along the way and keep them for use
    for i, text in enumerate(N.headline.values):
        if i == new_i: # starting a new sourceId group, have to look ahead to see where it ends and gather assetNameIds
            HPL.assets = set()
            while new_i<len(sourceIds) and sourceIds[new_i]==sourceIds[i]:
                if inHeadline[new_i]:
                    HPL.assets.add(assetNameIds[new_i])
                new_i += 1
        HPL.self = assetNameIds[i]
        
        tag = hTags[i]
        text = text.strip()
        if tag and text[:len(tag)]==tag:
            _has_tag = True
            text = text[len(tag):].lstrip()
            if text[0] in '-–—:':
                text = text[1:]
                text = text.lstrip()
        else:
            _has_tag = False
            
        ret[i] = compose(HPL.wordify,HPL.match_stocks,HPL.postproc)(text)
        
        if _has_tag:
#             ret[i] = [fr'\htag\{hTagIds[i]}.', r'\htag\conn.'] + ret[i]
            ret[i] = fr' \htag\{hTagIds[i]}.  \htag\conn. ' + ret[i]
        
    N['headlineWords'] = ret

#### go do it

In [37]:
%%time
N = _N_small.pipe(lambda N: N[N.assetNameId.isin(assetNameMapCodes)])
transform_headlines(N=N)

CPU times: user 3min 5s, sys: 1.18 s, total: 3min 6s
Wall time: 3min 6s


In [50]:
_N_.to_pickle(big_data/'trans/N1010.pkl')

#### let's see the results

In [38]:
seeN = N.pipe(sample(10))

In [39]:
seeN[['assetName','assetCodes','headlineTag','headline']]

assetName  \
7300577                Covidien Ltd   
7309262                Celgene Corp   
7314338        Bank of America Corp   
7362110                  DexCom Inc   
7368600                  Xencor Inc   
7509370         GlaxoSmithKline PLC   
7513857               Interoil Corp   
7514585                 Macerich Co   
7518041                  Pfizer Inc   
7548929  Auspex Pharmaceuticals Inc   

                                               assetCodes  \
7300577                               {'COV.BE', 'COV.N'}   
7309262                  {'CELG.O', 'CELG.OQ', 'CGNC.DE'}   
7314338                                  {'BAC', 'BAC.N'}   
7362110                             {'DXCM.OQ', 'DXCM.O'}   
7368600                             {'XNCR.OQ', 'XNCR.O'}   
7509370  {'GSK.L', 'GSK.F', 'GSK.DE', 'GSKy.DE', 'GSK.N'}   
7513857                                         {'IOC.N'}   
7514585                                         {'MAC.N'}   
7518041                      {'PFE.N', 'PFE.DE', 'PFE.F'}   
7548929                                        {'ASPX.O'}   

                   headlineTag  \
7300577                          
7309262                          
7314338               UPDATE 2   
7362110                          
7368600  U.S. RESEARCH ROUNDUP   
7509370                          
7513857                          
7514585                          
7518041                          
7548929                          

                                                                                                                   headline  
7300577                                             REG - Arrowgrass Capital Covidien plc - ISE Only - Covidien PLC <COV.N>  
7309262                               Hogging the Limelight: New Research on Netlist, Celgene, Jamba, Citigroup and Tilly's  
7314338                                                  UPDATE 2-Citigroup profit falls on legal and restructuring charges  
7362110                              DexCom to Present at 4th Annual Leerink Partners Global Healthcare Conference <DXCM.O>  
7368600                                                                      U.S. RESEARCH ROUNDUP- Alibaba, Google, Amazon  
7509370                   SANOFI <SASY.PA>: CREDIT SUISSE RAISES PRICE TARGET TO 104 EUROS FROM 94 EUROS; RATING OUTPERFORM  
7513857                                                                            INTEROIL ANNOUNCES POSITIVE 2014 RESULTS  
7514585                                            MACERICH BOARD ANNOUNCES GOVERNANCE CHANGES TO PROTECT STOCKHOLDER VALUE  
7518041  NIMBUS THERAPEUTICS SAYS COMPANY'S SERIES A INVESTORS, INCLUDING ATLAS VENTURE, SR ONE, LILLY VENTURES AND BILL...  
7548929                                                                Reuters Insider - Stocks climb more than one percent

In [40]:
seeN.headlineWords

7300577                              reg  -  arrowgrass  capital  \asset\self.  -  ise  only  -  \asset\self.  \ticker\self. 
7309262      hogging  the  limelight  :  new  research  on  netlist  ,  \asset\self.  ,  jamba  ,  \asset.  and  tilly  '  s 
7314338                               \htag\10.  \htag\conn.  \asset.  profit  falls  on  legal  and  restructuring  charges 
7362110         \asset\self.  to  present  at  4th  annual  leerink  partners  global  healthcare  conference  \ticker\self. 
7368600                                                              \htag\151.  \htag\conn.  \asset.  ,  google  ,  \asset. 
7509370     sanofi  \ticker.  :  credit  suisse  raises  price  target  to  \count\2.  euros  from  \count\2.  euros  ;  r...
7513857                                                                   \asset\self.  announces  positive  \year.  results 
7514585                                 \asset\self.  board  announces  governance  changes  to  protect  stockholder 

#### see more crap

In [377]:
N.headlineTag.value_counts()

                          39501
BRIEF                      4013
UPDATE 1                   3602
US STOCKS                  2160
UPDATE 2                   1964
US RESEARCH SUMMARY        1600
RPT                        1266
STOCKS NEWS US             1054
UPDATE 3                   1035
FACTBOX                     645
ANALYSIS                    626
HEADLINE STOCKS             602
PRESS DIGEST                539
TEXT                        535
SNAPSHOT                    524
CORRECTED                   480
UPDATE 4                    439
CANADA STOCKS               390
US STOCKS SNAPSHOT          378
WRAPUP 1                    322
TAKE A LOOK                 307
INTERVIEW                   305
WRAPUP 2                    272
Japan Hot Stocks            263
REFILE                      243
WRAPUP 3                    207
PREVIEW                     201
ADR Report                  161
STOCKS NEWS EUROPE          159
UPDATE 5                    134
DEALTALK                    127
Swiss st

In [395]:
theN = _N_
for tag, head in zip(theN.headlineTag, theN.headline):
    if tag and head.strip()[:len(tag)+1] not in [tag+'-',tag+':'] and head.strip()[:len(tag)+2] != tag+' -':
        print(f'TAG{{{tag}}} HEAD{{{head}}}')
        print(head.strip()[:len(tag)+2], '!=', tag+' -')

TAG{NYMEX} HEAD{NYMEX <NMX.N>- crude oil futures volume record}
NYMEX < != NYMEX -
TAG{NYMEX} HEAD{NYMEX <NMX.N> -- To buy stake in Optionable}
NYMEX < != NYMEX -
TAG{New Issue} HEAD{New Issue  -American General Finance sells $600 mln}
New Issue   != New Issue -
TAG{UPDATE} HEAD{UPDATE – UPCOMING DEADLINE: LEVI & KORSINSKY, LLP Notifies Investors of Class Action Against Alcobra Ltd. and Its Board of Directors and a Lead Plaintiff Deadline of January 20, 2015 -- ADHD <ADHD.O>}
UPDATE – != UPDATE -
TAG{UPDATE} HEAD{UPDATE – UPCOMING DEADLINE: LEVI & KORSINSKY, LLP Notifies Investors of Class Action Against Vivint Solar, Inc. and Its Board of Directors and a Lead Plaintiff Deadline of January 20, 2015 <VSLR.N>}
UPDATE – != UPDATE -
TAG{UPDATE} HEAD{UPDATE – UPCOMING DEADLINE: LEVI & KORSINSKY, LLP Notifies Investors of Class Action Against FireEye, Inc. and Its Board of Directors and a Lead Plaintiff Deadline of January 26, 2015 <FEYE.O>}
UPDATE – != UPDATE -
TAG{UPDATE} HEAD{UPDATE – DEA

In [403]:
len(N)

65509

In [402]:
((_N_.firstMentionSentence==1) & (_N_.assetNameId.isin(assetNameMapCodes))).sum(), _N_.shape[0]

(3872830, 9328750)

In [404]:
(3872830/65509)*40 / 60

39.41270156263516

In [271]:
# the row index is 1547548
row

time           sourceTimestamp  \
1547548 2009-01-15 18:43:11+00:00 2009-01-15 18:43:11+00:00   

                     firstCreated          sourceId  \
1547548 2009-01-15 18:30:09+00:00  70570c369ddd5b1a   

                                                                                                                   headline  \
1547548  GENERAL MOTORS <GM.N> SAYS ITS U.S. HOURLY MANUFACTURING COSTS HAVE DECLINED TO AN ESTIMATED $8 BLN IN 2008, ES...   

         urgency  takeSequence provider  \
1547548        1            16     RTRS   

                                                                                                                   subjects  \
1547548  {'MRG', 'AUTO', 'MTG', 'CYCS', 'DBT', 'BACT', 'CDM', 'JOB', 'US', 'USC', 'AUT', 'RTRS', 'CARM', 'DEAL', 'DRV', ...   

                                                     audiences  bodySize  \
1547548  {'PCO', 'T', 'PCU', 'U', 'D', 'M', 'RNP', 'E', 'NAT'}         0   

         companyCount headlineTag  marketCommentary  sentenceCount  wordCount  \
1547548             1                         False              1         27   

                                  assetCodes              assetName  \
1547548  {'GM.N', 'GRM.N', 'GMS.N', 'GPM.N'}  Motors Liquidation Co   

         firstMentionSentence  relevance  sentimentClass  sentimentNegative  \
1547548                     1        1.0              -1           0.811499   

         sentimentNeutral  sentimentPositive  sentimentWordCount  \
1547548           0.12971           0.058791                  27   

         noveltyCount12H  noveltyCount24H  noveltyCount3D  noveltyCount5D  \
1547548                0                0               0               0   

         noveltyCount7D  volumeCounts12H  volumeCounts24H  volumeCounts3D  \
1547548               0               33               36             137   

         volumeCounts5D  volumeCounts7D assetNameId  assetNamesCount  \
1547548             312             364        7203                1   

         firstMentionFixed               groupbyTime  
1547548                  1 2009-01-15 22:00:00+00:00

#### see which companies haven't found match

In [104]:
N = _N_

In [52]:
N['headlineList'] = N.headlineWords.map(str.split)
N['inHeadline'] = N.headlineList.map(lambda x: r'\asset\self.' in x)

CPU times: user 25.7 s, sys: 3.11 s, total: 28.8 s
Wall time: 28.7 s


In [105]:
Nnomatch = N.pipe(lambda N: N[(N.firstMentionSentence==1) & ~N.inHeadline & N.assetNameId.isin(assetNameMapCodes)])

In [107]:
nomatch = Nnomatch.assetNameId.value_counts()
nomatch.index.name, nomatch.name = nomatch.name, 'Count'

In [233]:
nomatch.reset_index(drop=True)#.plot();

0       15336
1        9985
2        9964
3        9878
4        9344
5        9164
6        8224
7        7780
8        7593
9        7467
10       7369
11       6457
12       6091
13       6079
14       5730
15       5679
16       5582
17       5064
18       4818
19       4651
20       4384
21       4012
22       3859
23       3770
24       3769
25       3494
26       3275
27       3229
28       3164
29       3039
30       2952
31       2930
32       2921
33       2867
34       2863
35       2833
36       2753
37       2696
38       2669
39       2560
40       2473
41       2461
42       2412
43       2270
44       2255
45       2204
46       2151
47       2007
48       1993
49       1983
50       1944
51       1940
52       1885
53       1875
54       1875
55       1821
56       1781
57       1779
58       1683
59       1618
60       1599
61       1593
62       1548
63       1490
64       1488
65       1460
66       1455
67       1446
68       1424
69       1385
70       1372
71    

In [357]:
(Nnomatch, nomatch, lookup) = pd.read_pickle('stock-help.pkl')

In [390]:
nomatch_i = 99
asset = nomatch.index[nomatch_i]
seeN = Nnomatch.pipe(lambda N: N[N.assetNameId==asset])
print(assetNameIdAssign.series.loc[asset])
seeN.headline.pipe(ljust)

Flex Ltd


53903      Next Inning Technology Previews Earnings for SiRF Technology, Flextronics International,... <SLAB.O><FLEX.O><HR...
54659      FLEXTRONICS INTERNATIONAL LTD.                                                                                 ...
54661      FLEXTRONICS INTERNATIONAL LTD <FLEX.O> Q3 NON-GAAP SHR $0.20                                                   ...
54668      FLEXTRONICS INTERNATIONAL LTD <FLEX.O> Q3 SHR $0.23 EXCLUDING ITEMS                                            ...
54675      Flextronics Announces Third Quarter Record Results <FLEX.O>                                                    ...
54679      FLEXTRONICS INTERNATIONAL LTD <FLEX.O> REUTERS ESTIMATES Q3 SHR VIEW $0.22                                     ...
54693      RPT-FLEXTRONICS INTERNATIONAL LTD <FLEX.O> Q3 SHR $0.23 EXCLUDING ITEMS                                        ...
54705      FLEXTRONICS INTERNATIONAL LTD <FLEX.O> SEES Q4 REVENUE AT ABOUT $4.8 BILLION                               

In [377]:
what = 24536
_N_.loc[what-1:what+1+1]

time           sourceTimestamp  \
24535 2007-01-16 22:31:18+00:00 2007-01-16 22:31:18+00:00   
24536 2007-01-16 22:31:18+00:00 2007-01-16 22:31:18+00:00   
24537 2007-01-16 22:31:34+00:00 2007-01-16 22:31:34+00:00   
24538 2007-01-16 22:31:58+00:00 2007-01-16 22:31:58+00:00   

                   firstCreated          sourceId  \
24535 2007-01-16 22:30:57+00:00  7d9666055def0ccf   
24536 2007-01-16 22:30:57+00:00  7d9666055def0ccf   
24537 2007-01-16 22:30:20+00:00  17b3ae118093971f   
24538 2007-01-16 22:31:58+00:00  5c23311c475412af   

                                                                                                headline  \
24535  ONEOK PARTNERS LP <OKS.N> SAYS HAS INCREASED ITS QUARTERLY CASH DISTRIBUTION TO 98 CENTS PER UNIT   
24536  ONEOK PARTNERS LP <OKS.N> SAYS HAS INCREASED ITS QUARTERLY CASH DISTRIBUTION TO 98 CENTS PER UNIT   
24537                                         RENASANT CORP <RNST.O> REUTERS ESTIMATES Q4 SHR VIEW $0.43   
24538       Spherion Updates Fourth Quarter 2006 Earnings Guidance and Schedules Conference Call <SFN.N>   

       urgency  takeSequence provider  \
24535        1             2     RTRS   
24536        1             2     RTRS   
24537        1             4     RTRS   
24538        3             1      PRN   

                                                 subjects  \
24535                 {'US', 'ELG', 'NGS', 'RTRS', 'LEN'}   
24536                 {'US', 'ELG', 'NGS', 'RTRS', 'LEN'}   
24537  {'FIN', 'RESF', 'US', 'RES', 'BNK', 'RTRS', 'LEN'}   
24538       {'NEWR', 'RESF', 'BACT', 'RES', 'DPR', 'LEN'}   

                    audiences  bodySize  companyCount headlineTag  \
24535  {'ELN', 'O', 'E', 'U'}         0             2               
24536  {'ELN', 'O', 'E', 'U'}         0             2               
24537              {'E', 'U'}         0             1               
24538                 {'PRN'}      7331             1               

       marketCommentary  sentenceCount  wordCount             assetCodes  \
24535             False              1         16              {'OKS.N'}   
24536             False              1         16              {'OKE.N'}   
24537             False              1         10  {'RNST.OQ', 'RNST.O'}   
24538             False             45       1147              {'SFN.N'}   

               assetName  firstMentionSentence  relevance  sentimentClass  \
24535  ONEOK Partners LP                     1        1.0               0   
24536          ONEOK Inc                     1        1.0               0   
24537      Renasant Corp                     1        1.0               0   
24538      SFN Group LLC                     1        1.0               1   

       sentimentNegative  sentimentNeutral  sentimentPositive  \
24535           0.202568          0.600913           0.196519   
24536           0.202568          0.600913           0.196519   
24537           0.016425          0.806599           0.176976   
24538           0.208569          0.328809           0.462622   

       sentimentWordCount  noveltyCount12H  noveltyCount24H  noveltyCount3D  \
24535                  16                2                2               2   
24536                  16                2                2               2   
24537                  10                2                2               2   
24538                 700                0                0               0   

       noveltyCount5D  noveltyCount7D  volumeCounts12H  volumeCounts24H  \
24535               2               2                2                2   
24536               2               2                2                2   
24537               2               2                3                3   
24538               0               0                0                0   

       volumeCounts3D  volumeCounts5D  volumeCounts7D assetNameId  \
24535               2               2               2        2057   
24536               2               2               2

In [381]:
oks, oke = M[M.assetCode=='OKS.N'], M[M.assetCode=='OKE.N']

In [387]:
oks.set_index('time').returnsOpenNextMktres10.corr(oke.set_index('time').returnsOpenNextMktres10)

0.6580509598009644

## just looking

In [183]:
for name in _N_.assetName.unique():
    print(name)

PetroChina Co Ltd
Travelers Companies Inc
Wal-Mart Stores Inc
Google Inc
XM Satellite Radio Holdings Inc
Sirius XM Radio Inc
Walt Disney Co
Microsoft Corp
Yahoo! Inc
Tenet Healthcare Corp
Siebert Financial Corp
Monsanto Co
Constellation Brands Inc
Rite Aid Corp
Cyren Ltd
Qualcomm Inc
Siemens AG
Internet Gold Golden Lines Ltd
Goldman Sachs Group Inc
Merrill Lynch & Co Inc
Citigroup Inc
General Electric Co
Time Warner Inc
Twenty-First Century Fox Inc
Viacom Inc
Sony Corp
BHP Billiton Ltd
Ryanair Holdings PLC
Fomento Economico Mexicano SAB de CV
Sanofi SA
AU Optronics Corp
Taiwan Semiconductor Manufacturing Co Ltd
Royal Bank of Scotland Group PLC
Hutchison Telecommunications International Ltd
Indosat Tbk PT
Korea Electric Power Corp
Nasdaq Inc
Kookmin Bank
Woori Finance Holdings Co Ltd
Honda Motor Co Ltd
LG Display Co Ltd
Apple Inc
Adobe Systems Inc
China Mobile Ltd
HSBC Holdings PLC
Willis Towers Watson PLC
Banco Santander SA
Daimler AG
Titanium Metals Corp
Companhia Siderurgica Nacional

Tellurian Inc
Del Monte Foods Co
Borders Group Inc
Allergan Finance LLC
Medifast Inc
KP Pharmaceuticals LLC
Jack in the Box Inc
Cigna Corp
Kelly Services Inc
SFN Group LLC
Hope Bancorp Inc
McEwen Mining Inc
SQBG Inc
FEI Co
Endo Health Solutions Inc
Hungarian Telephone And Cable Corp
Newmont Mining Corp
Here Holding Corp
Mair Holdings Inc
NiSource Inc
Astora Women's Health Holdings LLC
Mountain Province Diamonds Inc
Oil States International Inc
Lifetime Brands Inc
Schmitt Industries Inc
Fleetwood Enterprises Inc
A. O. Smith Corp
Western Union Co
Imperial Oil Ltd
Pepco Holdings LLC
Ingredion Inc
Unisys Corp
SAP AG
BEA Systems Inc
Sonde Resources Corp
Occidental Petroleum Corp
Buca Inc
Abaxis Inc
VF Corp
Grupo Aeroportuario del Pacifico SAB de CV
Colonial Properties Trust
Mentor Graphics Corp
LSI Industries Inc
Rexnord-Zurn Holdings Inc
Microsemi Corp Memory and Storage Solutions
Taseko Mines Ltd
Associated Banc-Corp
Potlatch Corp
Compania Cervecerias Unidas SA
Polymet Mining Corp
Central

Butler National Corp
Hemagen Diagnostics Inc
Gungnir Resources Inc
Avigen Inc
Electro Rent Corp
MGT Capital Investments Inc
Ultrapetrol (Bahamas) Ltd
NII Holdings Inc
C&F Financial Corp
Edwards Lifesciences Corp
Donaldson Company Inc
Veramark Technologies Inc
SRC Liquidation LLC
DNP Select Income Fund Inc
American Medical Alert Corp
Rand Capital Corp
Minrad International Inc
Glen Rose Petroleum Corp
Delcath Systems Inc
Cleco Corporate Holdings LLC
Genlyte Group Inc
Alliance HealthCare Services Inc
Yadkin Financial Corp
LL&E Royalty Trust
Tortoise Energy Infrastructure Corp
Tortoise North American Energy Corp
Camco Financial Corp
Quality Distribution Inc
Britton & Koontz Capital Corp
Zilog Inc
Champion Enterprises Inc
Sturm Ruger & Company Inc
TIB Financial Corp
Datawatch Corp
Integrated Silicon Solution Inc
MTM Technologies Inc
Magyar Bancorp Inc
Farmers National Bancorp
Smart & Final LLC
North Central Bancshares Inc
Catalina Marketing Corp
Eagle Rock Energy Partners LP
Devcon Internat

Northwest Airlines Corp
Clean Energy Fuels Corp
LDK Solar Co Ltd
Fuwei Films Holdings Co Ltd
PimCo Municipal Advantage Fund InCorp
PIMCO Income Strategy Fund II
PIMCO Income Strategy Fund
Allianzgi Convertible & Income Fund
Allianzgi Convertible & Income Fund II
PIMCO New York Municipal Income Fund II
PIMCO California Municipal Income Fund II
PIMCO Municipal Income Fund III
PIMCO California Municipal Income Fund Iii
Pimco New York Municipal Income Fund III
PIMCO Municipal Income Fund
PIMCO California Municipal Income Fund
PIMCO New York Municipal Income Fund
Nuveen Core Equity Alpha Fund
Nuveen Diversified Currency Opportunities Fund
Alpine Global Dynamic Dividend Fund
Gpc Biotech AG
TomoTherapy Inc
Neuro-Hitech Inc
Response Genetics Inc
Starent Networks LLC
WaferGen Bio-Systems Inc
Towerstream Corp
DGT Holdings Corp
Florida Gaming Corp
Infinera Corp
Deutsche Global High Income Fund Inc
FBR & Co
Yingli Green Energy Holding Co Ltd
Limelight Networks Inc
Boss Holdings Inc
Chang-On Intern

Palo Alto Networks Inc
Chuy's Holdings Inc
Natural Grocers By Vitamin Cottage Inc
Northern Tier Energy LP
E2open LLC
Horizon Therapeutics Inc
Del Frisco's Restaurant Group Inc
Globus Medical Inc
Howard Bancorp Inc
Eloqua Inc
Xylem Inc
Bloomin' Brands Inc
Peregrine Semiconductor Corp
Tronox Ltd
Manchester United PLC
Performant Financial Corp
Engility Holdings Inc
Hi Crush Partners LP
CU Bancorp
Sandstorm Gold Ltd
IF Bancorp Inc
Seven Arts Entertainment Inc
Trulia LLC
National Bank Holdings Corp
Capital Bank Financial Corp
Emerald Oil Inc
Corts Trust Weyerhauser Co
Pareteum Corp
Qualys Inc
Summit Midstream Partners LP
ADT Corp
Kraft Foods Group Inc
LifeLock Inc
JAVELIN Mortgage Investment Corp
Tile Shop Holdings Inc
W. P. Carey Inc
Berry Global Group Inc
Regulus Therapeutics Inc
Fleetmatics Group Ltd
Blackrock Municipal 2030 Target Term Trust
Ryman Hospitality Properties Inc
Amira Nature Foods Ltd
Realogy Holdings Corp
RLJ Entertainment Inc
Shutterstock Inc
Kythera Biopharmaceuticals Inc

In [297]:
_N_.pipe(lambda N: N.headline[N.assetNameId==7760].pipe(ljust))

20772     Asia Netcom in $636 mln trans-Pacific cable project                                                            ...
91927     PRESS DIGEST - Singapore newspapers - Feb 14                                                                   ...
290017    Singapore Hot Stocks-STATS ChipPAC in focus amid bid speculation                                               ...
321336    Pacific Internet to restate results from 2000 to 2006                                                          ...
322182    CONNECT HOLDINGS SAYS TO DATE, THERE ARE NO ALTERNATIVE OFFERS OR CONCRETE PROPOSALS AVAILABLE TO ALL SHAREHOLD...
322183    CONNECT HOLDINGS SAYS REVISED OFFER PRICE FOR PACIFIC INTERNET <PCNTF.O> REPRESENTS AN INCREASE OF 10 PCT FROM ...
324658    PRESS DIGEST - Singapore newspapers - June 8                                                                   ...
474706    PACIFIC INTERNET LTD <PCNTF.O> SAYS CEO PHEY TECK MOH TO STEP DOWN - SEC FILING                                ...


# Explore

In [94]:
/pd.DataFrame sorted(set(zip(M.assetCode,M.assetName)))

0               \
0               A.N   
1              AA.N   
2             AAI.N   
3             AAL.O   
4          AAMRQ.OB   
5             AAN.N   
6            AAON.O   
7             AAP.N   
8            AAPL.O   
9             AAT.N   
10            AAV.N   
11           AAVL.O   
12           AAWW.O   
13             AB.N   
14           ABAX.O   
15            ABB.N   
16           ABBV.N   
17            ABC.N   
18           ABCB.O   
19           ABCO.O   
20            ABD.N   
21           ABEV.N   
22            ABG.N   
23            ABI.N   
24            ABM.N   
25           ABMD.O   
26            ABT.N   
27            ABV.N   
28           ABVT.N   
29            ABX.N   
30            ABY.N   
31            ABY.O   
32           ACAD.O   
33           ACAS.O   
34           ACAT.O   
35            ACC.N   
36           ACCL.O   
37           ACCO.N   
38            ACE.N   
39           ACET.O   
40            ACF.N   
41           ACGL.O   
42            ACH.N   
43           ACHC.O   
44           ACHN.O   
45           ACIA.O   
46           ACIW.O   
47            ACL.N   
48            ACM.N   
49            ACN.N   
50            ACO.N   
51           ACOM.O   
52           ACOR.O   
53            ACS.N   
54           ACTG.O   
55           ACTS.O   
56           ACTV.N   
57            ACW.N   
58           ACXM.O   
59             AD.N   
60           ADBE.O   
61            ADC.N   
62           ADCT.O   
63            ADI.N   
64            ADI.O   
65            ADM.N   
66           ADNT.N   
67            ADP.N   
68            ADP.O   
69           ADPT.N   
70           ADRO.O   
71            ADS.N   
72           ADSK.O   
73            ADT.N   
74           ADTN.O   
75           ADVS.O   
76            AEA.N   
77            AEC.N   
78            AEE.N   
79            AEG.N   
80           AEGN.O   
81           AEGR.O   
82           AEIS.O   
83            AEL.N   
84            AEM.N   
85            AEO.N   
86           AEOS.O   
87            AEP.N   
88            AER.N   
89           AERI.O   
90            AES.N   
91            AET.N   
92            AEZ.A   
93             AF.N   
94           AFAM.O   
95           AFFX.O   
96           AFFY.O   
97            AFG.N   
98            AFL.N   
99            AFR.N   
100          AFSI.O   
101            AG.N   
102          AGAM.O   
103          AGCO.N   
104           AGE.N   
105           AGI.N   
106          AGII.O   
107          AGIO.O   
108           AGN.N   
109          AGNC.O   
110           AGO.N   
111           AGR.N   
112          AGRO.N   
113           AGU.N   
114          AGYS.O   
115            AH.N   
116           AHG.N   
117          AHGP.O   
118           AHL.N   
119           AHS.N   
120           AHT.N   
121         AIBYY.O   
122        AIBYY.OB   
123           AIG.N   
124          AIMC.O   
125          AIMT.O   
126           AIN.N   
127          AINV.O   
128          AIPC.O   
129           AIR.N   
130          AIRM.O   
131          AIRV.O   
132           AIT.N   
133           AIV.N   
134          AIXG.O   
135           AIZ.N   
136           AJG.N   
137          AJRD.N   
138          AKAM.O   
139           AKG.A   
140           AKR.N   
141          AKRX.O   
142           AKS.N   
143            AL.N   
144           ALB.N   
145           ALD.N   
146          ALDR.O   
147          ALDW.N   
148           ALE.N   
149          ALEX.N   
150          ALGN.O   
151          ALGT.O   
152           ALJ.N   
153           ALK.N   
154          ALKS.O   
155           ALL.N   
156          ALLE.N   
157          ALLT.O   
158          ALLY.N   
159          ALNY.O   
160           ALO.N   
161           ALR.N   
162          ALRM.O   
163          ALSK.O   
164          ALSN.N   
165          ALTE.O   
166          ALTH.O   
167          ALTR.O   
168           ALU.N   
169           ALV.N   
170          ALXN.O   
171           ALY.N   
172            AM.N   
173

In [119]:
N[N.assetNamesCount==2].headline.pipe(ljust)

1521196    SNAPSHOT - Financial Crisis - 0045 GMT                                                                         ...
1521197    SNAPSHOT - Financial Crisis - 0045 GMT                                                                         ...
1521199    UPDATE 2-GM gets $4 bln rescue loan, Chrysler on hold                                                          ...
1521200    UPDATE 2-GM gets $4 bln rescue loan, Chrysler on hold                                                          ...
1521202    RPT-India's TCS sees back office deals                                                                         ...
1521203    RPT-India's TCS sees back office deals                                                                         ...
1521204    IBM in sales alliance with Japan's Ricoh - paper                                                               ...
1521205    IBM in sales alliance with Japan's Ricoh - paper                                                           

In [150]:
N.loc[[1527026,1527027]]

time                      sourceTimestamp            \
1527026 2009-01-07 04:10:50+00:00 2009-01-07 04:10:50+00:00   
1527027 2009-01-07 04:10:50+00:00 2009-01-07 04:10:50+00:00   

        firstCreated              sourceId           \
1527026 2009-01-07 04:10:50+00:00  06a6b51052ef9c67   
1527027 2009-01-07 04:10:50+00:00  06a6b51052ef9c67   

        headline                                            urgency  \
1527026  UPDATE 2-Bank of America sells $2.8 bln CCB stake  3         
1527027  UPDATE 2-Bank of America sells $2.8 bln CCB stake  3         

         takeSequence provider  \
1527026  1             RTRS      
1527027  1             RTRS      

        subjects                                                                                                             \
1527026  {'MRG', 'DE', 'ISU', 'FINS', 'INVS', 'SG', 'COFS', 'RTRS', 'MEVN', 'EMRG', 'BUS', 'BNK', 'FIN', 'FUND', 'EUROPE...   
1527027  {'MRG', 'DE', 'ISU', 'FINS', 'INVS', 'SG', 'COFS', 'RTRS', 'MEVN', 'EMRG', 'BUS', 'BNK', 'FIN', 'FUND', 'EUROPE...   

        audiences                                                                         \
1527026  {'Z', 'UKI', 'T', 'DNP', 'PSC', 'U', 'D', 'M', 'EMK', 'RNP', 'NAW', 'PTD', 'E'}   
1527027  {'Z', 'UKI', 'T', 'DNP', 'PSC', 'U', 'D', 'M', 'EMK', 'RNP', 'NAW', 'PTD', 'E'}   

         bodySize  companyCount headlineTag  marketCommentary  sentenceCount  \
1527026  3737      4             UPDATE 2    False             27              
1527027  3737      4             UPDATE 2    False             27              

         wordCount assetCodes                                      \
1527026  709            {'UBS.N', 'UBSN.DE', 'UBSN.VX', 'UBSN.F'}   
1527027  709        {'IKM.N', 'IKL.N', 'BAC.N', 'IKJ.N', 'IKR.N'}   

        assetName              firstMentionSentence  relevance  \
1527026                UBS AG  15                    0.09759     
1527027  Bank of America Corp   1                    1.00000     

         sentimentClass  sentimentNegative  sentimentNeutral  \
1527026  1               0.112890           0.159270           
1527027 -1               0.722047           0.184978           

         sentimentPositive  sentimentWordCount  noveltyCount12H  \
1527026  0.727840            97                 0                 
1527027  0.092975           581                 4                 

         noveltyCount24H  noveltyCount3D  noveltyCount5D  noveltyCount7D  \
1527026  0                0               0               0                
1527027  4                4               4               4                

         volumeCounts12H  volumeCounts24H  volumeCounts3D  volumeCounts5D  \
1527026  13               23               32              36               
1527027  18               19               50              62               

         volumeCounts7D assetNameId  assetNamesCount  firstMentionFixed  \
1527026   56             8948        2                15                  
1527027  100              141        2                 1                  

        groupbyTime                
1527026 2009-01-07 22:00:00+00:00  
1527027 2009-01-07 22:00:00+00:00

##### loose stuff

In [21]:
re.findall(r'<[A-Z]+[a-z]*.?[A-Z]*>', '<AAPL.O> hi <WHAa.N>')

['<AAPL.O>', '<WHAa.N>']

In [85]:
def iter_tickers(N):
    re_ticker = re.compile(r'<[A-Z]*[a-z]*.?[A-Z]*>')
    for head in N.headline:
        yield from re_ticker.findall(head)
tickers = set(t[1:-1] for t in iter_tickers(_N_))

In [29]:
codes = {(a[:a.index('.')] if '.' in a else a): a for a in assetCodeIdAssign.series}

In [81]:
codes['USE']

KeyError: 'USE'

In [84]:
for code in assetCodeIdAssign.series:
    if any('a'<=x<='z' for x in code):
        print(code)

BFb.N
CMGb.N
HUBb.N
MWAb.N
PBRa.N
RDSa.N
RDSb.N
TRYb.N
VIAb.N
TIa.N
RGAa.N
RGAb.N
EBRb.N
JWa.N
MOGa.N
BRKb.N
PRISb.N
VALEp.N
FCEa.N
UAc.N
LGFb.N


In [ ]:
corpFullWords = {
    'Incorporated': 'Inc',
    'Corporation': 'Corp',
    'Company': 'Co',
    'Limited': 'Ltd',
    'Limited Liability Company': 'LLC',
    'Public Limited Company': 'PLC',
    'Limited Partnership': ['LP', 'L P'],
    'Companies': 'Cos',
    'Societe anonyme': ['SA','S A'],
    'Naamloze vennootschap': ['NV', 'N V'],
    # AS A/S ASA full names don't show up in news
    'Aktiengesellschaft': 'AG',
}
corpWords = set('Inc ,Inc Corp Co Ltd ,Ltd LLC ,LLC PLC ,PLC LP ,LP Cos SA ,SA NV ,NV ASA A/S AS PAO AG'.split())
corpWords |= set(['S A',', S A','L P','P L C','N V','SA de CV',',SA de CV'])
corpSpecial = 'set(Co Company Cos Companies'.split())

In [366]:
pd.Series(list(filter(lambda x: x.lower()[-2:]=='nv', assetNameIdAssign.series)))

0                                 Aegon NV
1                       AerCap Holdings NV
2                  Anheuser Busch Inbev NV
3         Chicago Bridge & Iron Company NV
4                     Core Laboratories NV
5                             ING Groep NV
6                   Koninklijke Philips NV
7                          Schlumberger NV
8                    STMicroelectronics NV
9                              Unilever NV
10                           CNH Global NV
11                               Eurand NV
12                                Mylan NV
13                                 Relx NV
14                              Crucell NV
15                             Cimpress NV
16                   NXP Semiconductors NV
17            LyondellBasell Industries NV
18                               Yandex NV
19                    InterXion Holding NV
20                     AVG Technologies NV
21                         ASML Holding NV
22                 Franks International NV
23         

filtering news to see patterns; see if anything

In [65]:
re_dot = re.compile(r'[a-tv-zA-TV-Z]\.[a-rt-zA-RT-Z]')
re_ticker = re.compile(r'<[A-Z]+[a-z]*\.[A-Z]+>')
re_money = re.compile(r'\$[0-9]+(,[0-9][0-9][0-9])*\.[0-9][0-9][0-9]')
#symb = Counter()
for head in _N_.headline:
    #symb += Counter(head)
    if '¢' in (re_ticker.sub('', head).replace('.','')).lower():
        print(head)

99¢ Only Stores Reports Total Sales of $351.1 Million for the Third Quarter of Fiscal 2009 Ended December 27, 2008 <NDN.N>
99¢ Only Stores Will Sell 9 Apple iPod Nanos for Only 99¢ Each to Celebrate the Grand Opening of Its Newest 99¢ Only Stores on Thursday, January 22nd, 2009, in Norwalk, California <NDN.N>
99¢ Only Stores to Report Third Quarter Fiscal 2009 Financial Results on February 4, 2009 <NDN.N>
99¢ ONLY STORES� ANNOUNCES SUSPENSION OF EXIT FROM TEXAS MARKET TO RE-EVALUATE ITS TEXAS OPERATIONS IN LIGHT OF A SIGNIFICANT IMPROVEMENT IN JANUARY SALES RESULTS AND THE POTENTIAL BENEFICIAL OPPORTUNITIES RESULTING FROM A RECESSIONARY ECON
99¢ Only Stores Announces Suspension of Exit from Texas Market to Re-evaluate its Texas Operations in Light of a Significant Improvement in January Sales Results and the Potential Beneficial Opportunities Result <NDN.N>
99¢ ONLY STORES� REPORTS THIRD QUARTER FISCAL 2009 FINANCIAL RESULTS
99¢ Only Stores Reports Third Quarter Fiscal 2009 Financial R

99¢ Only Stores Will Sell 22\\" Sylvania Flat Screen LCD TVs for Only 99 Cents Each to Celebrate the Grand Opening of Its 99¢ Only Stores Thousand Oaks Location in San Antonio, Texas, on Friday the 13th of August <NDN.N>
99¢ Only Stores Reports $0.24 EPS for Q1 Fiscal 2011 versus $0.14 for Q1 Fiscal 2010 <NDN.N>
99¢ Only Stores Will Sell 19\\" Flat Screen LCD TVs for Only 99 Cents Each to the First 9 Customers to Celebrate the Grand Opening of Its First 99¢ Only Stores in Artesia, California, on Friday the 13th of August <NDN.N>
Common Cents Mobile Hosts 7¢ Appetizers at Black Bear Saloon August 25, 2010 <S.N>
99¢ Only Stores Will Sell 22\\" Phillips Flat Screen LCD TVs for Only 99 Cents Each to the First 9 Customers to Celebrate the Grand Opening of the New 99¢ Only Stores Location in North Hollywood, California on Th <NDN.N>
99¢ Only Stores to Sell Gallons of Milk for Only 89¢ in all of its Dallas-Fort Worth, Texas Stores Starting Saturday, September 18 <NDN.N>
99¢ Only Stores Will S

INTERCONTINENTAL HOTELS GROUP PLC <IHG.L> - TOTAL DIVIDEND PER SHARE 64.0¢, UP 16 PCT
Sturm, Ruger & Company, Inc. Reports 2012 Fully Diluted Earnings of $3.60 Per Share and Declares Dividend of 40.4¢ Per Share <RGR.N>
STURM, RUGER & COMPANY, INC. REPORTS FIRST QUARTER FULLY DILUTED EARNINGS OF $1.20 PER SHARE AND DIVIDEND OF 49¢ PER SHARE
Sturm, Ruger & Company, Inc. Reports First Quarter Fully Diluted Earnings of $1.20 Per Share and Dividend of 49¢ Per Share <RGR.N>
TARGA RESOURCES CORP <TRGP.N> SAYS BOARD OF DIRECTORS HAS DECLARED A QUARTERLY CASH DIVIDEND OF 53.25¢ PER SHARE
STURM, RUGER & COMPANY, INC. REPORTS SECOND QUARTER FULLY DILUTED EARNINGS OF $1.63 PER SHARE AND DIVIDEND OF 65¢ PER SHARE
Sturm, Ruger & Company, Inc. Reports Second Quarter Fully Diluted Earnings of $1.63 Per Share and Dividend of 65¢ Per Share <RGR.N>
INTERCONTINENTAL HOTELS GROUP PLC <IHG.L> - 10% INCREASE IN THE INTERIM DIVIDEND TO 23¢
RPT-INTERCONTINENTAL HOTELS GROUP PLC <IHG.L> - 10% INCREASE IN THE IN

Sturm, Ruger & Company, Inc. Reports 2015 Fully Diluted Earnings of $3.21 Per Share and Declares Dividend of 35¢ Per Share <RGR.N>
STURM, RUGER & COMPANY, INC. REPORTS 2015 FULLY DILUTED EARNINGS OF $3.21 PER SHARE AND DECLARES DIVIDEND OF 35¢ PER SHARE
STURM RUGER & CO INC <RGR.N> SAYS BOARD OF DIRECTORS DECLARED A DIVIDEND OF 35¢ PER SHARE FOR THE FOURTH QUARTER
STURM, RUGER & COMPANY, INC. REPORTS 2015 FULLY DILUTED EARNINGS OF $3.21 PER SHARE AND DECLARES DIVIDEND OF 35¢ PER SHARE
STURM, RUGER & COMPANY, INC. REPORTS FIRST QUARTER DILUTED EARNINGS OF $1.21 PER SHARE AND DECLARES DIVIDEND OF 48¢ PER SHARE
Sturm, Ruger & Company, Inc. Reports First Quarter Diluted Earnings of $1.21 Per Share and Declares Dividend of 48¢ Per Share <RGR.N>
ALASKA AIR GROUP INC SEES Q2 COST PER ASM EXCLUDING ITEMS 8.00¢ - 8.05¢
Carriage Services Raises Quarterly Cash Dividend To 5¢/QTR <CSV.N>
CARRIAGE SERVICES RAISES QUARTERLY CASH DIVIDEND TO 5¢/QTR
CARRIAGE SERVICES INC <CSV.N> SAYS BOARD HAS APPROVE

In [61]:
pd.DataFrame([t for t in symb.most_common() if t[0] not in ' abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ0123456789'])

0        1
0    .  9361350
1    -  7011447
2    >  4418923
3    <  4418899
4    ,  4295058
5    $  2368578
6    '  1110070
7    :   900175
8    /   752278
9    &   542335
10   \   507947
11   ;   364738
12   (   292008
13   )   291053
14   "   253729
15   %   189517
16   ’    26693
17   ?    26081
18   `    25941
19   �    24092
20   +    22996
21   [    14308
22   ]    14252
23   ®    13363
24   !    11172
25   _     9277
26   *     6673
27   é     5285
28   –     4602
29   ™     4430
30   ”     4180
31   “     4149
32         3505
33   £     3407
34   #     2901
35   =     2619
36   ‘     1763
37   É     1489
38   ó     1021
39   ú     1008
40   @      882
41   Ú      818
42   α      642
43   ο      596
44   í      594
45   ε      576
46   Ç      570
47   ι      560
48   à      533
49   á      515
50   Ó      512
51   |      503
52   Α      494
53   ν      491
54   ã      490
55   τ      482
56   σ      468
57   è      463
58   ç      456
59   Ã      454
60   ö      445
61   Ν      428
62   Å      394
63   κ      367
64   —      366
65   ä      357
66   ñ      357
67   ρ      353
68   ü      347
69   η      327
70   Á      317
71   ¢      311
72   Ö      302
73   å      301
74   μ      295
75   Ø      294
76   Ο      280
77   π      274
78   Ü      271
79   υ      267
80   Õ      264
81   …      263
82   ς      259
83   €      251
84   ½      247
85   Σ      247
86   Í      234
87   λ      226
88   Κ      223
89   Ι      220
90   ø      219
91   Η      218
92   Ñ      217
93   ή      216
94   Ω      214
95   ά      205
96   Ε      175
97   Ä      174
98   γ      166
99   ί      161
100  ô      156
101  Τ      146
102  §      142
103  õ      141
104  έ      132
105  ´      132
106  ì      128
107  ω      123
108  ê      122
109  θ      122
110  ¼      113
111  ℠      112
112  Â      109
113  δ      108
114  ë      108
115  ï      102
116  ~       95
117  ό       92
118  ¾       92
119  ώ       87
120  Ê       87
121  ζ       87
122  È       87
123  °       84
124  Ô       81
125  À       76
126  χ       75
127  Ì       75
128  ⅝       69
129  ©       69
130  ύ       67
131  Æ       63
132  Ï       57
133  ß       47
134  β       47
135  æ       40
136  φ       37
137  ξ       36
138  ^       35
139  â       33
140  Δ       32
141  −       32
142  ē       31
143  ¡       30
144  ─       30
145  Μ       29
146  ¥       28
147  Ë       24
148  ²       24
149  Π       23
150  ±       23
151  º       23
152  ⅞       22
153  ¹       21
154  {       18
155  }       18
156         17
157  µ       16
158  «       16
159  »       16
160  ·       15
161  ▼       15
162  ‐       15
163  î       14
164  •       14
165  ­       14
166         13
167  ‑       13
168  ⅛       12
169  Γ       11
170  ψ       11
171  ù       11
172  û       10
173  Β       10
174  ⅜       10
175         10
176  ¤        9
177  Έ        9
178  有        8
179  的        8
180  ı        8
181          8
182  ³        7
183  Ⓡ        7
184  ΄        6
185  
        6
186  Χ        6
187          6
188          5
189  Ρ        5
190          5
191          5
192  ¨        5
193  ‎        5
194  ∙        5
195  Θ        4
196  Î        4
197  蓋        4
198  特        4
199  納        4
200  稱        4
201  銀        4
202  行        4
203  能        4
204  可        4
205  資        4
206  Υ        4
207  Φ        4
208  ū        4
209  ▒        4
210  и        4
211  а        4
212  ン        4
213          4
214  ―        4
215  ́        4
216  ◊        4
217  ≈        4
218  ΐ        3
219  合        3
220  性        3
221  Λ        3
222  ы        3
223  л        3
224  в        3
225  ト        3
226  ク        3
227  、        3
228  ˈ        3
229          2
230  所        2
231  格        2
232  都        2
233  申        2
234  請        2
235  政        2
236  府        2
237  轉        2
238  換        2
239  優        2
240  先        2
241  股        2
242  並        2
243  非        2
244  只        2
245  最        2
246  大        2
247  家        2
248  才        2
249  

In [91]:
test = pd.read_pickle(the_data/'given/test.pkl')

In [99]:
for t, (__, NN, ____) in enumerate(test):
    smapi = {}
    for i, src in enumerate(NN.sourceId):
        if src in smapi and smapi[src] != i-1:
            print(t, smapi[src], i)
        smapi[src] = i

In [86]:
pd.Series(list(tickers-set(assetCodeIdAssign.series)))

0              SILD.L
1              SSPH.L
2              PINN.O
3              MDME.L
4              LARD.L
5              KEL.TO
6               CEO.L
7               SAL.O
8          PVASTAT.AX
9               EFF.N
10              DHG.N
11            CAGR.PA
12             GEMS.O
13           NHLDD.OB
14             LII.TO
15              PEO.N
16            UVIC.PK
17            ERCS.WA
18             MMZ.TO
19              ICS.N
20           CCTYQ.PK
21             IGAS.L
22            UBSVX.N
23              PGP.N
24            BPTH.OB
25              SMO.V
26              PNS.A
27            MRPL.BO
28             ATSC.A
29            BOKF.OQ
30            CTICD.O
31              TVL.V
32             WWW.TO
33             AGIL.O
34             VMT.AX
35           ABGek.MC
36             CWBS.O
37              RAS.L
38            ADAV.AD
39             AERO.O
40               PQ.N
41             WHLM.O
42              BVM.L
43              JSN.N
44              ACG.L
45        

# Scratch

In [39]:
'FDK' in codes

False

In [45]:
pd.set_option('display.max_colwidth', 115)

In [50]:
pd.set_option('display.max_colwidth', 115)
N[N.firstMentionSentence==1][['assetName','headline']].pipe(sample(5000)).pipe(ljust_c('headline'))

assetName  \
1521238                                                 Bank of America Corp   
1521247                                                 Bank of America Corp   
1521255                                                       Microsoft Corp   
1521329                                               KB Financial Group Inc   
1521336                                                               BP PLC   
1521347                                                     Eli Lilly and Co   
1521361                                                     Deutsche Bank AG   
1521372                                                      Tata Motors Ltd   
1521405                                             Lloyds Banking Group PLC   
1521425                                                          Stantec Inc   
1521442                                              New Energy Exchange Ltd   
1521445                                Federal National Mortgage Association   
1521449                                      Western Asset Premier Bond Fund   
1521452                                        International Game Technology   
1521464                                              Janus Capital Group Inc   
1521465                                                            BB&T Corp   
1521471                                                       Albemarle Corp   
1521474                                            National Instruments Corp   
1521476                                            National Instruments Corp   
1521487                                                       Albemarle Corp   
1521488                                                       Albemarle Corp   
1521490                                            National Instruments Corp   
1521511                                              Goldman Sachs Group Inc   
1521514                                      Federal Home Loan Mortgage Corp   
1521527                                                     Wells Fargo & Co   
1521533                                                           Nucor Corp   
1521546                                                     Wells Fargo & Co   
1521547                                         Thermo Fisher Scientific Inc   
1521551                                               NovaGold Resources Inc   
1521590                                                           Siemens AG   
1521593                                                HUSA Liquidating Corp   
1521594                                                           EZCORP Inc   
1521597                                       Magellan Midstream Holdings LP   
1521600                                            National Instruments Corp   
1521606                                                         Barclays PLC   
1521659                                                   Legacy Bancorp Inc   
1521676                                              American Greetings Corp   
1521701                            Dreyfus Strategic Municipal Bond Fund Inc   
1521712                                                      Tata Motors Ltd   
1521729               Advent Claymore Convertible Securities and Income Fund   
1521731            Advent Claymore Convertible Securities and Income Fund II   
1521733                              Fiduciary/Claymore MLP Opportunity Fund   
1521734  Western Asset/Claymore Inflation-Linked Opportunities & Income Fund   
1521737                                              American Greetings Corp   
1521738                                   Canadian Imperial Bank of Commerce   
1521744                                           Charter Communications Inc   
1521768                                                        Ford Motor Co   
1521776                                               E*TRADE Financial Corp   
1521777                                                              DIRECTV   
1521822                                                            